In [24]:
import vtk

class DistanceToPointFilter(vtk.vtkPolyDataAlgorithm):
    """
    A custom filter that computes the Euclidean distance of each point in a vtkPolyData
    to a specified target point in 3D space. The distances are stored as a scalar array.
    
    Usage:
        distance_filter = DistanceToPointFilter()
        distance_filter.SetInputConnection(somePolyDataSource.GetOutputPort())
        distance_filter.SetTargetPoint(1.0, 2.0, 3.0)
        distance_filter.Update()
        outputPolyData = distance_filter.GetOutput()
    """

    def __init__(self):
        super().__init__()
    
        # By default, VTK doesn't have automatic new-style class initialization in Python.
        # We'll make sure we set up the input and output ports properly.
        # Note: VTK may handle input/output ports automatically; in some cases,
        # you might need to call SetNumberOfInputPorts(1) / SetNumberOfOutputPorts(1).
        # Initialize the target point. Users can modify this via SetTargetPoint().
    
        self.TargetPoint = [0.0, 0.0, 0.0]
    
    def SetTargetPoint(self, x, y, z):
        """
        Sets the 3D coordinates of the target point from which distances will be calculated.
        """
        self.TargetPoint = [float(x), float(y), float(z)]
    
        # Mark the pipeline as modified so changes propagate
    
        self.Modified()
    
    def GetTargetPoint(self):
        """
        Returns the current target point as a tuple (x, y, z).
        """
        return tuple(self.TargetPoint)
    
    def RequestData(self, request, inInfo, outInfo):
        """
        The main execution method where the filter processes input vtkPolyData
        and produces an output with a scalar distance array.
        """
        print("Asdfasf")
        print(inInfo, outInfo)
        # 1. Retrieve the input and output data objects from the pipeline.
        input_data = vtk.vtkPolyData.GetData(inInfo[0])
        output_data = vtk.vtkPolyData.GetData(outInfo)
    
        # 2. Copy the input to the output. 
        output_data.ShallowCopy(input_data)
    
        # 3. Get the number of points in the polygonal data.
        num_points = input_data.GetNumberOfPoints()
    
        # 4. Create a new vtkFloatArray to store the distance values for each point.
        distances = vtk.vtkFloatArray()
        distances.SetName("DistanceToTarget")
        distances.SetNumberOfComponents(1)
        distances.SetNumberOfTuples(num_points)
    
        # 5. Compute distances for each point and store them in the array.
        tx, ty, tz = self.TargetPoint
        for i in range(num_points):
            px, py, pz = input_data.GetPoint(i)
            dx = px - tx
            dy = py - ty
            dz = pz - tz
            distance = (dx2 + dy2 + dz2) * 0.5
            distances.SetValue(i, distance)
    
        # 6. Attach the array to the output's point data. Also set it as the active scalar.
        output_data.GetPointData().AddArray(distances)
        output_data.GetPointData().SetScalars(distances)
    
        return 1


In [25]:
sphere = vtk.vtkSphereSource()
sphere.SetRadius(1.0)
sphere.SetThetaResolution(30)
sphere.SetPhiResolution(30)
sphere.Update()

# Create and configure the distance filter
filter = DistanceToPointFilter()
filter.SetInputConnection(sphere.GetOutputPort())
filter.SetTargetPoint(2.0, 0.0, 0.0)  # Target point outside the sphere
filter.Update()
output = filter.GetOutput()

In [23]:
import pyvista as pv
mesh = pv.wrap(output)
mesh

PolyData (0x7f121cbc36a0)
  N Cells:    0
  N Points:   0
  N Strips:   0
  X Bounds:   1.000e+299, -1.000e+299
  Y Bounds:   1.000e+299, -1.000e+299
  Z Bounds:   1.000e+299, -1.000e+299
  N Arrays:   0

In [21]:
pv.wrap(sphere.GetOutput())

PolyData (0x7f121cbc33a0)
  N Cells:    1680
  N Points:   842
  N Strips:   0
  X Bounds:   -9.985e-01, 9.985e-01
  Y Bounds:   -9.931e-01, 9.931e-01
  Z Bounds:   -1.000e+00, 1.000e+00
  N Arrays:   1